In [1]:
import os
import pandas as pd
import numpy as np
import sys
sys.path.append('../../Scripts')
from preprocess_daily import DailyPreprocessor
from generate_signals import SignalGenerator

비보호좌회전, 신호우회전, 유턴

줄임말 목록
- `i` : 교차로번호, `inter_no`
- `f` : 진입, from, `inc_edge_id`
- `t` : 진출, to, `out_edge_id`
- `vec` : 방향벡터, unit vector (`np.array([0.6, 0.8])`)
- `dire` : 방위, direction (동, 서, 남, 북, 북동, 북서, 남동, 남서)
- `rvec` : 정방향 방향벡터, unit vector to the right direction (`np.array([0,1])`)

필요한 객체들 목록

- `i2dire2rvec` : `inter_no` $\mapsto$ `dire2rvec`
  - `dire2rvec` : `dire` $\mapsto$ `rvec`
- `i2f` : `inter_no` $\mapsto$ `f_edges`
- `i2t` : `inter_no` $\mapsto$ `t_edges`
- `i2f2dire` : `inter_no` $\mapsto$ `f21dire`
  - `f2dire` : `from_edge` $\mapsto$ `dire`
- `i2t2dire` : `inter_no` $\mapsto$ `t21dire`
  - `t2dire` : `to_edge` $\mapsto$ `dire`

In [2]:
self = DailyPreprocessor()
self.main()

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.
2. 중간산출물을 생성합니다.
2-1. 매칭 테이블들을 생성했습니다.
2-2. 비보호우회전(g)을 배정했습니다.
2-3. 직진 및 좌회전(G)을 배정했습니다.
2-2. node2num_cycles.json를 저장했습니다.
3. 이슈사항을 저장합니다.


In [3]:
display(self.match4.head())
display(self.match5.head())

inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle out_angle
0       175         1         A        8        남        북       179       179
1       175         1         B        4        북        남       001       001
2       175         2         A        7        북        동       001       001
3       175         2         B        3        남        서       179       179
4       175         3         A        6        동        서       090       090

inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
0       175         1         A        8        남        북       179   
1       175         1         B        4        북        남       001   
2       175         2         A        7        북        동       001   
3       175         2         B        3        남        서       179   
4       175         3         A        6        동        서       090   

  out_angle    inc_edge_id   out_edge_id node_id  
0       179  -571542797_02  571542797_02      i0  
1       001  -571500487_01  571500487_01      i0  
2       001  -571500487_01  571500487_01      i0  
3       179  -571542797_02  571542797_02      i0  
4       090   571545870_02  571545870_01      i0

In [4]:
self.load_data()
self.get_matches()

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.


1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.
2-1. 매칭 테이블들을 생성했습니다.


In [9]:
self.match6[:60]

inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
0        175         1         A        8        남        북       179   
1        175         1         B        4        북        남       001   
2        175         2         A        7        북        동       001   
3        175         2         B        3        남        서       179   
4        175         3         A        6        동        서       090   
5        175         3         B        1        동        남       090   
6        175         4         A        5        서        북       270   
7        175         4         B        2        서        동       270   
8        175         1         A        8        남        북       179   
9        175         1         B        4        북        남       001   
10       175         2         A        7        북        동       001   
11       175         2         B        3        남        서       179   
12       175         3         A        6        동        서       090   
13       175         3         B        1        동        남       090   
14       175         4         A        5        서        북       270   
15       175         4         B        2        서        동       270   
16       176         1         A        8        남        북       180   
17       176         1         B        4        북        남       359   
18       176         2         A        8        남        북       180   
19       176         2         B        3        남        서       180   
20       176         3         A        5        서        북       270   
21       176         3         B       18      NaN      NaN       NaN   
22       177         1         A        8        남        북       179   
23       177         1         B        4        북        남       000   
24       177         2         A        7        북        동       000   
25       177         2         B        3        남        서       179   
26       177         3         A       17      NaN      NaN       NaN   
27       177         3         B       18      NaN      NaN       NaN   
28       177         4         A        5        서        북       268   
29       177         4         B        1        동        남       090   
30       177         1         A        8        남        북       179   
31       177         1         B        4        북        남       000   
32       177         2         A        7        북        동       000   
33       177         2         B        3        남        서       179   
34       177         3         A       17      NaN      NaN       NaN   
35       177         3         B       18      NaN      NaN       NaN   
36       177         4         A        5        서        북       268   
37       177         4         B        1        동        남       090   
38       178         1         A       20      NaN      NaN       NaN   
39       178         1         B       20      NaN      NaN       NaN   
40       178         2         A       20      NaN      NaN       NaN   
41       178         2         B       20      NaN      NaN       NaN   
42       178         3         A       20      NaN      NaN       NaN   
43       178         3         B       20      NaN      NaN       NaN   
44       178         4         A       20      NaN      NaN       NaN   
45       178         4         B       20      NaN      NaN       NaN   
46       178         1         A        8        남        북       180   
47       178         1         B        4        북        남       000   
48       178         2         A        7        북        동       000   
49       178         2         B        3        남        서       180   
50       178         3         A        5        서        북       270   
51       178         3         B        2        서        동       270   
52       178         4         A        6        동        서       090   
53       178         4         B        1        동        남   

In [6]:
self.matching

inter_no  move_no inc_dire out_dire       inc_edge_id    out_edge_id  \
0        175        1        동        남      571545870_02   571500487_01   
1        175        2        서        동      571510153_02   571500487_01   
2        175        3        남        서     -571542797_02   571542797_02   
3        175        4        북        남     -571500487_01   571500487_01   
4        175        5        서        북      571510153_02   571542797_02   
..       ...      ...      ...      ...               ...            ...   
71       210       21        북        서  571511538_02.121   571542115_01   
72       210       21        서        남   571500535_02.18   571511538_01   
73       210       21        남        동      571500585_02   571500535_01   
74       210       21        동        북     -571542115_01   571500535_01   
75       210        5        서        북      571500535_02  -571500535_02   

   node_id  
0       i0  
1       i0  
2       i0  
3       i0  
4       i0  
..     ...  
71      i6  
72      i6  
73      i6  
74      i6  
75     u60  

[76 rows x 7 columns]